# Assignment: Segmenting and Clustering Neighborhoods in Toronto
### part 3 of 3
*by Miguel Rozsas*


## abstract
In this assignment, you will be required to explore, segment, and cluster the neighborhoods in the city of Toronto based on the postalcode and borough information.. However, unlike New York, the neighborhood data is not readily available on the internet. What is interesting about the field of data science is that each project can be challenging in its unique way, so you need to learn to be agile and refine the skill to learn new libraries and tools quickly depending on the project.

For the Toronto neighborhood data, a Wikipedia page exists that has all the information we need to explore and cluster the neighborhoods in Toronto. You will be required to scrape the Wikipedia page and wrangle the data, clean it, and then read it into a pandas  dataframe so that it is in a structured format like the New York dataset.

Once the data is in a structured format, you can replicate the analysis that we did to the New York City dataset to explore and cluster the neighborhoods in the city of Toronto.

### Start by importing the relevant libraries and the file saved in previous session

In [1]:
import numpy as np # library for vectorized computation
import pandas as pd # library to process data as dataframes       
import requests # library to handle requests

## Import the DataFrame saved in part 2 of this assignment.
file= 'Coursera-Capstone_2of3.csv'
df_merged= pd.read_csv(file)
df_merged.drop ('Unnamed: 0', axis=1, inplace=True)
df_merged.head ()

PostalCode           Borough                                Neighbourhood  \
0        M3A        North York                                    Parkwoods   
1        M4A        North York                             Victoria Village   
2        M5A  Downtown Toronto                    Regent Park, Harbourfront   
3        M6A        North York             Lawrence Manor, Lawrence Heights   
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

### Explore and cluster the neighborhoods in Toronto.

Lets start with the necessary libraries

In [2]:

#!pip install geopy
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize


#! pip install folium==0.5.0
import folium # plotting library

print('Folium installed')
print('Libraries imported.')

interest= "Toronto, Ontario"
geolocator = Nominatim(user_agent="toronto_explorer")
toronto = geolocator.geocode(interest)
print('The coordinates of Toronto are {}, {}.'.format(toronto.latitude, toronto.longitude))

Folium installed
Libraries imported.
The coordinates of Toronto are 43.6534817, -79.3839347.


Toronto's map

In [3]:
map_Toronto = folium.Map(location=[toronto.latitude, toronto.longitude], zoom_start=12)
title_html = '''
             <h3 align="center" style="font-size:16px"><b>{}</b></h3>
             '''.format("neighbourhoods, boroughs and postal code in Toronto") 
map_Toronto.get_root().html.add_child(folium.Element(title_html))

# adding markers to map
for lat, lon, borough, neighbourhood, postal in zip(df_merged['Latitude'], df_merged['Longitude'], df_merged['Borough'], df_merged['Neighbourhood'], df_merged['PostalCode']):
    label = '{}, {} - {}'.format(neighbourhood, borough, postal)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=4,
        popup=label,
        color='blue',
        fill=True
        ).add_to(map_Toronto)  
    
map_Toronto

### Toronto's venues by neighbourhood
Using foursquare do get venues by neighbourhood 

In [4]:
# initialize my Foursquare credentials
CLIENT_ID = 'FZDPFCII3LOEUDNI2GETXZM2T2AFWPKWZMDP4VX5X3OK4DFH' # my Foursquare ID
CLIENT_SECRET = 'L314JHHIHHYXUSGEXJU1UZ5JSXOWNHACRNWAAD5EWPFHJO5Q' # my Foursquare Secret
ACCESS_TOKEN = 'YJ55TLGLG5XTRKKQ0PZZ1RVVWVZ4EK4BWJLS2ZCDA100YDVJ' # my FourSquare Access Token
VERSION = '20180604'
LIMIT = 30
print ("Foursquare credentilas are set.")

Foursquare credentilas are set.


Define a function to retrieve venues by latitudes and longitudes on the merged dataframe from above and returns a similar dataframe with the venue and category columns added to it.

In [5]:
def getNearbyVenues(df):
    # radius around the lat,lng
    radius=500

    # iterate over the input data frame using the lat, long of each Neighbourhood as an argument to Foursquare API to get the venues at that location.

    # define the base Foursquare API URL 
    base_url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}'

    venues_list=[]
    for i, r in df.iterrows ():
        postalCode= r['PostalCode']
        borough= r['Borough']
        nbhd= r['Neighbourhood']
        b_lat= r['Latitude'] 
        b_lng= r['Longitude']   
        #print("DEBUG: ", postalCode, nbhd)
        
        # create the API request URL
        url= base_url.format(CLIENT_ID, CLIENT_SECRET, VERSION, b_lat, b_lng, radius)
            
        # GET request
        result = requests.get(url)
        try:
            items= result.json()["response"]['groups'][0]['items']
        except KeyError:
            print ("KeyError: response has not groups or items. Check: ")
            print (result.json()["response"])
            quit ()

        # iterate over Foursquare data, get the vanue name and category
        for i in items:
            v= i['venue']       
            venue= (postalCode, borough, nbhd, b_lat, b_lng, v['name'], v['location']['lat'], v['location']['lng'], v['categories'][0]['name'])
            venues_list.append(venue)

    # return venues_list as a dataframe
    nearby= pd.DataFrame(data= venues_list, columns= ['PostalCode', 'Borough', 'Neighborhood', 'B_Lat', 'B_Long', 'Venue', 'V_Lat', 'V_Long', 'Category'])
    return(nearby)

In [10]:
print ("This may take a while...be patient")
torontoVenues= getNearbyVenues(df_merged)
print ("...done.")

This may take a while...be patient
...done.


Now, our dataframe nearbyVenues has borough data from 'https://cocl.us/Geospatial_data' (part 2) and venues names, coordinates and category from foursquare. Nice.

In [11]:
torontoVenues.head ()

PostalCode     Borough      Neighborhood      B_Lat     B_Long  \
0        M3A  North York         Parkwoods  43.753259 -79.329656   
1        M3A  North York         Parkwoods  43.753259 -79.329656   
2        M4A  North York  Victoria Village  43.725882 -79.315572   
3        M4A  North York  Victoria Village  43.725882 -79.315572   
4        M4A  North York  Victoria Village  43.725882 -79.315572   

                    Venue      V_Lat     V_Long               Category  
0         Brookbanks Park  43.751976 -79.332140                   Park  
1           Variety Store  43.751974 -79.333114      Food & Drink Shop  
2  Victoria Village Arena  43.723481 -79.315635           Hockey Arena  
3               Portugril  43.725819 -79.312785  Portuguese Restaurant  
4             Tim Hortons  43.725517 -79.313103            Coffee Shop

In [12]:
torontoVenues.shape

(1329, 9)

There are 1329 venues in our Toronto's dataset.

### Exploring the data.
As the question is open, there is no specific task and questions are just poping out of my mind at no particular order.

So, the first one that I can think is how many distinct categories are by borough ?

Which one is the most diverse bourogh ? Which is the lesser one ?


In [13]:
torontoCategGroupBy= torontoVenues.groupby ('Borough')['Category']
torontoCategGroupBy.nunique().nlargest (100)

Borough
Downtown Toronto    147
North York           90
West Toronto         73
Central Toronto      60
East Toronto         59
Scarborough          53
East York            47
Etobicoke            38
York                 16
Mississauga          12
Name: Category, dtype: int64

So, Downtown Toronto has the greatest number of distinct venues, and Mississauga is the lesser one.

Lets explore a particular bourogh, lets say, North York. What is the most common venue in North York ?

In [14]:
NorthYorkDF= torontoVenues[torontoVenues['Borough']=='North York']
NorthYorkDF['Category'].value_counts ()

Coffee Shop           17
Clothing Store        10
Pizza Place            8
Park                   7
Restaurant             7
                      ..
Deli / Bodega          1
Salon / Barbershop     1
Food Court             1
Convenience Store      1
Department Store       1
Name: Category, Length: 90, dtype: int64

So, the Coffe Shop is the most common venue in North York. Nice.

Lets list all the 17 Coffe Shops in North York.

In [15]:
NorthYorkDF[NorthYorkDF['Category']=='Coffee Shop'][['Venue', 'Neighborhood', 'V_Lat', 'V_Long']]

Venue                                     Neighborhood  \
4           Tim Hortons                                 Victoria Village   
42          Tim Hortons                 Lawrence Manor, Lawrence Heights   
146         Tim Hortons                                        Don Mills   
156       Delimark Cafe                                        Don Mills   
349           Starbucks  Bathurst Manor, Wilson Heights, Downsview North   
352         Tim Hortons  Bathurst Manor, Wilson Heights, Downsview North   
449           Starbucks                     Fairview, Henry Farm, Oriole   
454  Aroma Espresso Bar                     Fairview, Henry Farm, Oriole   
465         Tim Hortons                     Fairview, Henry Farm, Oriole   
466         Tim Hortons                     Fairview, Henry Farm, Oriole   
470         Tim Hortons                     Fairview, Henry Farm, Oriole   
474         Tim Hortons                  Northwood Park, York University   
744         Tim Hortons                Bedford Park, Lawrence Manor East   
749           Starbucks                Bedford Park, Lawrence Manor East   
777           Starbucks                      Willowdale, Willowdale East   
790           Starbucks                      Willowdale, Willowdale East   
881         Tim Hortons                      Willowdale, Willowdale West   

         V_Lat     V_Long  
4    43.725517 -79.313103  
42   43.719427 -79.467995  
146  43.722897 -79.339117  
156  43.727536 -79.339547  
349  43.755797 -79.440471  
352  43.754767 -79.443250  
449  43.777990 -79.344091  
454  43.777700 -79.344652  
465  43.774993 -79.346303  
466  43.777964 -79.344715  
470  43.775249 -79.347740  
474  43.764289 -79.488790  
744  43.735356 -79.419605  
749  43.732604 -79.419136  
777  43.768353 -79.413046  
790  43.768464 -79.414017  
881  43.780940 -79.444231

And how many distinct venues coordinates are in North York ?

In [16]:
ct= nearbyVenues[nearbyVenues['Borough']=='North York']
ct.groupby (['V_Lat', 'V_Long']).count ()

PostalCode  Borough  Neighborhood  B_Lat  B_Long  Venue  \
V_Lat     V_Long                                                                
43.705747 -79.442378           1        1             1      1       1      1   
43.707170 -79.442658           1        1             1      1       1      1   
43.707420 -79.443126           1        1             1      1       1      1   
43.709031 -79.444053           1        1             1      1       1      1   
43.709111 -79.443930           1        1             1      1       1      1   
...                          ...      ...           ...    ...     ...    ...   
43.801685 -79.363938           1        1             1      1       1      1   
43.803664 -79.363905           1        1             1      1       1      1   
43.804515 -79.366138           1        1             1      1       1      1   
43.805455 -79.364186           1        1             1      1       1      1   
43.805539 -79.360695           1        1             1      1       1      1   

                      Category  
V_Lat     V_Long                
43.705747 -79.442378         1  
43.707170 -79.442658         1  
43.707420 -79.443126         1  
43.709031 -79.444053         1  
43.709111 -79.443930         1  
...                        ...  
43.801685 -79.363938         1  
43.803664 -79.363905         1  
43.804515 -79.366138         1  
43.805455 -79.364186         1  
43.805539 -79.360695         1  

[202 rows x 7 columns]

There is 198 distinct coordinates only in North York.

### Show boroughs in Toronto's map
Lets create a map of Toronto showing the Boroughs.

We need to assign to each borough a unique color from the choosen colormap (cm.rainbow).

I will add an additional column, Borough_ID, to our nearbyVenues dataframe. This column is a unique ID for the borough and it is used as an index in the color map table.

Lets create 2 auxiliary lists: 

1. borough_list: which is a simple list of unique boroughs names 
1. borough_IDs: another simple list of integers, one by borough in the list above.

In [18]:
borough_IDs= [i for i in range (0, len (nearbyVenues.Borough.unique()))]
borough_list= torontoVenues.Borough.unique()

Now, using the 2 lists above, we can add the additional Borough_ID column to our dataframe.

In [19]:
torontoVenues['Borough_ID']= torontoVenues['Borough'].replace(to_replace=borough_list, value=borough_IDs, inplace=False)
torontoVenues.head ()

PostalCode     Borough      Neighborhood      B_Lat     B_Long  \
0        M3A  North York         Parkwoods  43.753259 -79.329656   
1        M3A  North York         Parkwoods  43.753259 -79.329656   
2        M4A  North York  Victoria Village  43.725882 -79.315572   
3        M4A  North York  Victoria Village  43.725882 -79.315572   
4        M4A  North York  Victoria Village  43.725882 -79.315572   

                    Venue      V_Lat     V_Long               Category  \
0         Brookbanks Park  43.751976 -79.332140                   Park   
1           Variety Store  43.751974 -79.333114      Food & Drink Shop   
2  Victoria Village Arena  43.723481 -79.315635           Hockey Arena   
3               Portugril  43.725819 -79.312785  Portuguese Restaurant   
4             Tim Hortons  43.725517 -79.313103            Coffee Shop   

   Borough_ID  
0           0  
1           0  
2           0  
3           0  
4           0

Plot the venues in each Neighbourhood using the Borough_ID as a index to a unique color and the borough center with the same color.

In [20]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# n= number of Boroughs
n= len (nearbyVenues.Borough.unique())

# create map
map_Toronto = folium.Map(location=[toronto.latitude, toronto.longitude], zoom_start=12)
title= "Venues by Neighborhood in Toronto"
title_html = '''
             <h3 align="center" style="font-size:16px"><b>{}</b></h3>
             '''.format(title) 
map_Toronto.get_root().html.add_child(folium.Element(title_html))

# set color scheme for the clusters
x = np.arange(n)
ys = [i + x + (i*x)**2 for i in range(n)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add venues to the map
for name, category, bid, v_lat, v_lon, in zip(torontoVenues['Venue'], torontoVenues['Category'], torontoVenues['Borough_ID'], torontoVenues['V_Lat'], torontoVenues['V_Long']):
    label = '{}: {}'.format(category, name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [v_lat, v_lon],
        radius=3,
        popup=label,
        color=rainbow[bid],
        fill=True,
        fill_color=rainbow[bid],
        fill_opacity=0.6).add_to(map_Toronto)

# add the borough centers to the map
for borough, nbhd, bid, pc, b_lat, b_lon, in zip(torontoVenues['Borough'], torontoVenues['Neighborhood'], torontoVenues['Borough_ID'], torontoVenues['PostalCode'], torontoVenues['B_Lat'], torontoVenues['B_Long']):
    label = '{}: {} ({})'.format(borough, nbhd, pc)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [b_lat, b_lon],
        radius=5,
        popup=label,
        color=rainbow[bid],
        fill=True,
        fill_color=rainbow[bid],
        fill_opacity=0.7).add_to(map_Toronto)
print ("done")

done


In [21]:
map_Toronto

Let's repeat the analyzes done in Manhattan, New York in Toronto. 

I will not restrict the analysis to one borough like it was done in Manhattan, New York.

Instead I will work with all Toronto data, as Manhattan, New York alone has 3166 venues and the entire Toronto has about one third than that. Check.


In [27]:
torontoVenues[['Category']].shape

(1329, 1)

In [28]:
torontoVenues.groupby('Neighborhood').count()

PostalCode  Borough  B_Lat  \
Neighborhood                                                                  
Agincourt                                                 4        4      4   
Alderwood, Long Branch                                    6        6      6   
Bathurst Manor, Wilson Heights, Downsview North          22       22     22   
Bayview Village                                           4        4      4   
Bedford Park, Lawrence Manor East                        24       24     24   
...                                                     ...      ...    ...   
Willowdale, Willowdale East                              30       30     30   
Willowdale, Willowdale West                               6        6      6   
Woburn                                                    4        4      4   
Woodbine Heights                                          8        8      8   
York Mills West                                           2        2      2   

                                                 B_Long  Venue  V_Lat  V_Long  \
Neighborhood                                                                    
Agincourt                                             4      4      4       4   
Alderwood, Long Branch                                6      6      6       6   
Bathurst Manor, Wilson Heights, Downsview North      22     22     22      22   
Bayview Village                                       4      4      4       4   
Bedford Park, Lawrence Manor East                    24     24     24      24   
...                                                 ...    ...    ...     ...   
Willowdale, Willowdale East                          30     30     30      30   
Willowdale, Willowdale West                           6      6      6       6   
Woburn                                                4      4      4       4   
Woodbine Heights                                      8      8      8       8   
York Mills West                                       2      2      2       2   

                                                 Category  Borough_ID  
Neighborhood                                                           
Agincourt                                               4           4  
Alderwood, Long Branch                                  6           6  
Bathurst Manor, Wilson Heights, Downsview North        22          22  
Bayview Village                                         4           4  
Bedford Park, Lawrence Manor East                      24          24  
...                                                   ...         ...  
Willowdale, Willowdale East                            30          30  
Willowdale, Willowdale West                             6           6  
Woburn                                                  4           4  
Woodbine Heights                                        8           8  
York Mills West                                         2           2  

[95 rows x 9 columns]

In [29]:
torontoVenues[['Category']]

Category
0                       Park
1          Food & Drink Shop
2               Hockey Arena
3      Portuguese Restaurant
4                Coffee Shop
...                      ...
1324          Hardware Store
1325    Fast Food Restaurant
1326           Tanning Salon
1327  Thrift / Vintage Store
1328                     Gym

[1329 rows x 1 columns]

In [30]:
print('There are {} uniques categories.'.format(len(torontoVenues['Category'].unique())))

There are 236 uniques categories.


In [31]:
type (torontoVenues)

pandas.core.frame.DataFrame

In [188]:
torontoVenues.shape

(1329, 10)

In [189]:
toronto_onehot = pd.get_dummies(torontoVenues[['Category']])
toronto_onehot.head ()

Category_Accessories Store  Category_Adult Boutique  Category_Airport  \
0                           0                        0                 0   
1                           0                        0                 0   
2                           0                        0                 0   
3                           0                        0                 0   
4                           0                        0                 0   

   Category_Airport Food Court  Category_Airport Gate  \
0                            0                      0   
1                            0                      0   
2                            0                      0   
3                            0                      0   
4                            0                      0   

   Category_Airport Lounge  Category_Airport Service  \
0                        0                         0   
1                        0                         0   
2                        0                         0   
3                        0                         0   
4                        0                         0   

   Category_Airport Terminal  Category_American Restaurant  \
0                          0                             0   
1                          0                             0   
2                          0                             0   
3                          0                             0   
4                          0                             0   

   Category_Antique Shop  ...  Category_Train Station  \
0                      0  ...                       0   
1                      0  ...                       0   
2                      0  ...                       0   
3                      0  ...                       0   
4                      0  ...                       0   

   Category_Vegetarian / Vegan Restaurant  Category_Video Game Store  \
0                                       0                          0   
1                                       0                          0   
2                                       0                          0   
3                                       0                          0   
4                                       0                          0   

   Category_Video Store  Category_Vietnamese Restaurant  \
0                     0                               0   
1                     0                               0   
2                     0                               0   
3                     0                               0   
4                     0                               0   

   Category_Warehouse Store  Category_Wine Bar  Category_Wings Joint  \
0                         0                  0                     0   
1                         0                  0                     0   
2                         0                  0                     0   
3                         0                  0                     0   
4                         0                  0                     0   

   Category_Women's Store  Category_Yoga Studio  
0                       0                     0  
1                       0                     0  
2                       0                     0  
3                       0                     0  
4                       0                     0  

[5 rows x 236 columns]

In [220]:
# one hot encoding
toronto_onehot = pd.get_dummies(torontoVenues[['Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = torontoVenues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.shape


(1329, 236)

In [221]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                         Agincourt          0.0   
1                            Alderwood, Long Branch          0.0   
2   Bathurst Manor, Wilson Heights, Downsview North          0.0   
3                                   Bayview Village          0.0   
4                 Bedford Park, Lawrence Manor East          0.0   
..                                              ...          ...   
90                      Willowdale, Willowdale East          0.0   
91                      Willowdale, Willowdale West          0.0   
92                                           Woburn          0.0   
93                                 Woodbine Heights          0.0   
94                                  York Mills West          0.0   

    Accessories Store  Adult Boutique  Airport  Airport Food Court  \
0                 0.0             0.0      0.0                 0.0   
1                 0.0             0.0      0.0                 0.0   
2                 0.0             0.0      0.0                 0.0   
3                 0.0             0.0      0.0                 0.0   
4                 0.0             0.0      0.0                 0.0   
..                ...             ...      ...                 ...   
90                0.0             0.0      0.0                 0.0   
91                0.0             0.0      0.0                 0.0   
92                0.0             0.0      0.0                 0.0   
93                0.0             0.0      0.0                 0.0   
94                0.0             0.0      0.0                 0.0   

    Airport Gate  Airport Lounge  Airport Service  Airport Terminal  ...  \
0            0.0             0.0              0.0               0.0  ...   
1            0.0             0.0              0.0               0.0  ...   
2            0.0             0.0              0.0               0.0  ...   
3            0.0             0.0              0.0               0.0  ...   
4            0.0             0.0              0.0               0.0  ...   
..           ...             ...              ...               ...  ...   
90           0.0             0.0              0.0               0.0  ...   
91           0.0             0.0              0.0               0.0  ...   
92           0.0             0.0              0.0               0.0  ...   
93           0.0             0.0              0.0               0.0  ...   
94           0.0             0.0              0.0               0.0  ...   

    Trail  Train Station  Vegetarian / Vegan Restaurant  Video Game Store  \
0     0.0            0.0                            0.0               0.0   
1     0.0            0.0                            0.0               0.0   
2     0.0            0.0                            0.0               0.0   
3     0.0            0.0                            0.0               0.0   
4     0.0            0.0                            0.0               0.0   
..    ...            ...                            ...               ...   
90    0.0            0.0                            0.0               0.0   
91    0.0            0.0                            0.0               0.0   
92    0.0            0.0                            0.0               0.0   
93    0.0            0.0                            0.0               0.0   
94    0.0            0.0                            0.0               0.0   

    Video Store  Vietnamese Restaurant  Warehouse Store  Wine Bar  \
0         0.000               0.000000              0.0       0.0   
1         0.000               0.000000              0.0       0.0   
2         0.000               0.000000              0.0       0.0   
3         0.000               0.000000              0.0       0.0   
4         0.000               0.000000              0.0       0.0   
..          ...                    ...              ...       ...   
90        0.000               0.033333              0.0     

In [222]:
toronto_grouped.shape

(95, 236)

In [223]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

           venue  freq
0     Pizza Place  0.33
1             Gym  0.17
2  Sandwich Place  0.17
3     Coffee Shop  0.17
4             Pub  0.17


----Bathurst Manor, Wilson Heights, Downsview North----
           venue  freq
0           Bank  0.09
1    Coffee Shop  0.09
2       Pharmacy  0.05
3   Intersection  0.05
4  Shopping Mall  0.05


----Bayview Village----
                 venue  freq
0                 Café  0.25
1                 Bank  0.25
2   Chinese Restaurant  0.25
3  Japanese Restaurant  0.25
4          Yoga Studio  0.00


----Bedford Park, Lawrence Manor East----
                  venue  freq
0           Coffee Shop  0.08
1        Sandwich Place  0.08
2    Italian Restaurant  0.08
3  Fast Food Restaurant  0.04
4       Thai Restaurant  0.04


----Berczy Park----
                venue  freq
0        Cocktail Bar  0.07
1  Seafood Restaurant  0.07
2      Farmers Market  0.07
3            Beer Bar  0.07
4         Coffee Shop  0.07


----Birch Cliff, Cliffside West----
         

In [224]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [225]:
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
toronto_grouped_sorted = pd.DataFrame(columns=columns)
toronto_grouped_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    toronto_grouped_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

toronto_grouped_sorted

Neighborhood  \
0                                         Agincourt   
1                            Alderwood, Long Branch   
2   Bathurst Manor, Wilson Heights, Downsview North   
3                                   Bayview Village   
4                 Bedford Park, Lawrence Manor East   
..                                              ...   
90                      Willowdale, Willowdale East   
91                      Willowdale, Willowdale West   
92                                           Woburn   
93                                 Woodbine Heights   
94                                  York Mills West   

        1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue  \
0   Latin American Restaurant                Lounge           Skating Rink   
1                 Pizza Place           Coffee Shop                    Gym   
2                 Coffee Shop                  Bank            Gas Station   
3                        Bank    Chinese Restaurant    Japanese Restaurant   
4              Sandwich Place    Italian Restaurant            Coffee Shop   
..                        ...                   ...                    ...   
90           Ramen Restaurant           Coffee Shop                   Café   
91                Pizza Place        Discount Store            Coffee Shop   
92                Coffee Shop          Soccer Field  Korean BBQ Restaurant   
93                       Park          Dance Studio             Beer Store   
94                       Park     Convenience Store          Women's Store   

   4th Most Common Venue 5th Most Common Venue  
0         Breakfast Spot           College Gym  
1         Sandwich Place                   Pub  
2     Chinese Restaurant           Bridal Shop  
3                   Café         Women's Store  
4              Juice Bar       Thai Restaurant  
..                   ...                   ...  
90        Sandwich Place           Pizza Place  
91               Butcher              Pharmacy  
92           Curling Ice             Drugstore  
93          Skating Rink              Bus Stop  
94           Curling Ice             Drugstore  

[95 rows x 6 columns]

In [226]:
toronto_grouped_sorted.shape

(95, 6)

### Clusterize the toronto data

In [227]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

# set number of clusters
kclusters = 10

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering init="k-means++", n_clusters=num_clusters, n_init=12)
kmeans = KMeans(init="k-means++", n_clusters=kclusters, n_init=12).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([4, 1, 1, 4, 1, 4, 4, 4, 4, 4, 0, 1, 4, 1, 4, 4, 1, 4, 4, 1, 1, 1,
       4, 1, 4, 4, 2, 1, 1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 1, 7, 4, 4, 1, 4,
       4, 4, 0, 1, 4, 8, 2, 4, 4, 4, 4, 4, 5, 1, 7, 4, 1, 0, 1, 4, 4, 0,
       4, 9, 4, 1, 6, 1, 4, 4, 1, 4, 4, 1, 1, 4, 4, 0, 1, 4, 4, 1, 3, 1,
       2, 4, 1, 1, 1, 4, 2], dtype=int32)

In [228]:
len (kmeans.labels_)

95

In [229]:
kmeans.cluster_centers_

array([[-4.33680869e-19,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  5.00000000e-02],
       [ 3.86624869e-03,  2.16840434e-19,  1.08420217e-19, ...,
         2.16840434e-19,  5.42101086e-19,  1.73472348e-18],
       [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       ...,
       [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00]])

In [230]:
kmeans.cluster_centers_[0].shape

(235,)

In [231]:
len (kmeans.cluster_centers_[0])

235

In [232]:
kmeans.cluster_centers_[0].shape

(235,)

In [233]:
centroid_labels = [kmeans.cluster_centers_[i] for i in kmeans.labels_]
len (centroid_labels[0])

235

In [234]:
# add clustering labels
toronto_grouped_sorted.insert(0, 'Cluster Labels', kmeans.labels_)


# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = torontoVenues.join(toronto_grouped_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

PostalCode     Borough      Neighborhood      B_Lat     B_Long  \
0        M3A  North York         Parkwoods  43.753259 -79.329656   
1        M3A  North York         Parkwoods  43.753259 -79.329656   
2        M4A  North York  Victoria Village  43.725882 -79.315572   
3        M4A  North York  Victoria Village  43.725882 -79.315572   
4        M4A  North York  Victoria Village  43.725882 -79.315572   

                    Venue      V_Lat     V_Long               Category  \
0         Brookbanks Park  43.751976 -79.332140                   Park   
1           Variety Store  43.751974 -79.333114      Food & Drink Shop   
2  Victoria Village Arena  43.723481 -79.315635           Hockey Arena   
3               Portugril  43.725819 -79.312785  Portuguese Restaurant   
4             Tim Hortons  43.725517 -79.313103            Coffee Shop   

   Borough_ID  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0           0               0                  Park     Food & Drink Shop   
1           0               0                  Park     Food & Drink Shop   
2           0               1           Pizza Place           Coffee Shop   
3           0               1           Pizza Place           Coffee Shop   
4           0               1           Pizza Place           Coffee Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0         Women's Store           Curling Ice             Drugstore  
1         Women's Store           Curling Ice             Drugstore  
2          Hockey Arena          Intersection     French Restaurant  
3          Hockey Arena          Intersection     French Restaurant  
4          Hockey Arena          Intersection     French Restaurant

In [235]:
columns= ['Borough', 'Neighborhood', 'Category', 'Cluster Labels']
toronto_merged[columns]

Borough                                       Neighborhood  \
0     North York                                          Parkwoods   
1     North York                                          Parkwoods   
2     North York                                   Victoria Village   
3     North York                                   Victoria Village   
4     North York                                   Victoria Village   
...          ...                                                ...   
1324   Etobicoke  Mimico NW, The Queensway West, South of Bloor,...   
1325   Etobicoke  Mimico NW, The Queensway West, South of Bloor,...   
1326   Etobicoke  Mimico NW, The Queensway West, South of Bloor,...   
1327   Etobicoke  Mimico NW, The Queensway West, South of Bloor,...   
1328   Etobicoke  Mimico NW, The Queensway West, South of Bloor,...   

                    Category  Cluster Labels  
0                       Park               0  
1          Food & Drink Shop               0  
2               Hockey Arena               1  
3      Portuguese Restaurant               1  
4                Coffee Shop               1  
...                      ...             ...  
1324          Hardware Store               4  
1325    Fast Food Restaurant               4  
1326           Tanning Salon               4  
1327  Thrift / Vintage Store               4  
1328                     Gym               4  

[1329 rows x 4 columns]

In [236]:
toronto_grouped_sorted.head ()

Cluster Labels                                     Neighborhood  \
0               4                                        Agincourt   
1               1                           Alderwood, Long Branch   
2               1  Bathurst Manor, Wilson Heights, Downsview North   
3               4                                  Bayview Village   
4               1                Bedford Park, Lawrence Manor East   

       1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Latin American Restaurant                Lounge          Skating Rink   
1                Pizza Place           Coffee Shop                   Gym   
2                Coffee Shop                  Bank           Gas Station   
3                       Bank    Chinese Restaurant   Japanese Restaurant   
4             Sandwich Place    Italian Restaurant           Coffee Shop   

  4th Most Common Venue 5th Most Common Venue  
0        Breakfast Spot           College Gym  
1        Sandwich Place                   Pub  
2    Chinese Restaurant           Bridal Shop  
3                  Café         Women's Store  
4             Juice Bar       Thai Restaurant

### plot the clusters on the map

In [237]:
def add_categorical_legend(folium_map, title, colors, labels):
    if len(colors) != len(labels):
        raise ValueError("colors and labels must have the same length.")

    color_by_label = dict(zip(labels, colors))
    
    legend_categories = ""     
    for label, color in color_by_label.items():
        legend_categories += f"<li><span style='background:{color}'></span>{label}</li>"
        
    legend_html = f"""
    <div id='maplegend' class='maplegend'>
      <div class='legend-title'>{title}</div>
      <div class='legend-scale'>
        <ul class='legend-labels'>
        {legend_categories}
        </ul>
      </div>
    </div>
    """
    script = f"""
        <script type="text/javascript">
        var oneTimeExecution = (function() {{
                    var executed = false;
                    return function() {{
                        if (!executed) {{
                             var checkExist = setInterval(function() {{
                                       if ((document.getElementsByClassName('leaflet-top leaflet-right').length) || (!executed)) {{
                                          document.getElementsByClassName('leaflet-top leaflet-right')[0].style.display = "flex"
                                          document.getElementsByClassName('leaflet-top leaflet-right')[0].style.flexDirection = "column"
                                          document.getElementsByClassName('leaflet-top leaflet-right')[0].innerHTML += `{legend_html}`;
                                          clearInterval(checkExist);
                                          executed = true;
                                       }}
                                    }}, 100);
                        }}
                    }};
                }})();
        oneTimeExecution()
        </script>
      """
   

    css = """

    <style type='text/css'>
      .maplegend {
        z-index:9999;
        float:right;
        background-color: rgba(255, 255, 255, 1);
        border-radius: 5px;
        border: 2px solid #bbb;
        padding: 10px;
        font-size:12px;
        positon: relative;
      }
      .maplegend .legend-title {
        text-align: left;
        margin-bottom: 5px;
        font-weight: bold;
        font-size: 90%;
        }
      .maplegend .legend-scale ul {
        margin: 0;
        margin-bottom: 5px;
        padding: 0;
        float: left;
        list-style: none;
        }
      .maplegend .legend-scale ul li {
        font-size: 80%;
        list-style: none;
        margin-left: 0;
        line-height: 18px;
        margin-bottom: 2px;
        }
      .maplegend ul.legend-labels li span {
        display: block;
        float: left;
        height: 16px;
        width: 30px;
        margin-right: 5px;
        margin-left: 0;
        border: 0px solid #ccc;
        }
      .maplegend .legend-source {
        font-size: 80%;
        color: #777;
        clear: both;
        }
      .maplegend a {
        color: #777;
        }
    </style>
    """

    folium_map.get_root().header.add_child(folium.Element(script + css))

    return folium_map

In [238]:
np.linspace(0, 1, 5)

array([0.  , 0.25, 0.5 , 0.75, 1.  ])

In [239]:
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(n)]
len (ys)
ys

[array([0, 1, 2, 3, 4, 5, 6, 7, 8, 9])]

In [240]:
kclusters

10

In [245]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# n= number of Boroughs
n= len (toronto_merged.Borough.unique())

# create map
map_clusters = folium.Map(location=[toronto.latitude, toronto.longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(n)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, venue, categ, cluster in zip(toronto_merged['V_Lat'], toronto_merged['V_Long'], toronto_merged['Venue'], toronto_merged['Category'], toronto_merged['Cluster Labels']):
    label_str= "{}:{}({})".format (categ, venue, cluster)
    popup = folium.Popup (label_str, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        color=rainbow[cluster],
        popup= popup,
        fill=True,
        fill_color=rainbow[cluster],
        fill_opacity=0.7).add_to(map_clusters)

# add a legend on the right upper corner
clusters_colors= []
clusters_legends= []
for cluster in range (kclusters):
    clusters_colors.append (rainbow[cluster])
    clusters_legends.append ("cluster {}". format (cluster))

map_clusters= add_categorical_legend(map_clusters, 'Clusters',
                             colors = clusters_colors,
                           labels = clusters_legends)
print ('done.')


done.


In [255]:
yyy

['cluster 0',
 'cluster 1',
 'cluster 2',
 'cluster 3',
 'cluster 4',
 'cluster 5',
 'cluster 6',
 'cluster 7',
 'cluster 8',
 'cluster 9']

In [247]:
map_clusters

In [292]:
t= 0
for i in range (kclusters):
    cluster= toronto_merged.loc[toronto_merged['Cluster Labels'] == i, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]
    cluster.reset_index(drop=True, inplace=True)
    n= len (cluster)
    t= t+n
    print ("cluster {} has {} venues and the most common venues in this cluster are:".format (i, n))
    most_common= []
    for v in cluster['1st Most Common Venue'].unique ():
        most_common.append (v)
    print (most_common)
    print ()
print ("the {} cluster sum {} venues.".format (kclusters, t))

cluster 0 has 15 venues and the most common venue in this cluster are:
['Park', 'River']

cluster 1 has 418 venues and the most common venue in this cluster are:
['Pizza Place', 'Coffee Shop', 'Sandwich Place', 'Furniture / Home Store', 'Bar', 'Ramen Restaurant', 'Indian Restaurant', 'Park', 'Dessert Shop', 'Fast Food Restaurant', 'Grocery Store']

cluster 2 has 11 venues and the most common venue in this cluster are:
['Park', 'Playground']

cluster 3 has 1 venues and the most common venue in this cluster are:
['Bakery']

cluster 4 has 872 venues and the most common venue in this cluster are:
['Coffee Shop', 'Clothing Store', 'Gym', 'Café', 'Park', 'Gastropub', 'Home Service', 'Restaurant', 'Trail', 'Grocery Store', 'Bakery', 'Golf Course', 'Hotel', 'Bar', 'Bank', 'Greek Restaurant', 'Fast Food Restaurant', 'American Restaurant', 'General Entertainment', 'Pool', 'Jewelry Store', 'Mexican Restaurant', 'Middle Eastern Restaurant', 'Gift Shop', 'Latin American Restaurant', 'Tennis Court',

In [290]:
cluster= toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]
cluster.reset_index(drop=True, inplace=True)
cluster['1st Most Common Venue'].unique ()

array(['Park', 'River'], dtype=object)

In [250]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough                           Venue      V_Lat     V_Long  \
0           North York                 Brookbanks Park  43.751976 -79.332140   
1           North York                   Variety Store  43.751974 -79.333114   
249               York                      Nairn Park  43.690654 -79.456300   
250               York                   Maximum Woman  43.690651 -79.456333   
251               York                  Fairbanks Pool  43.691959 -79.448922   
252               York          Fairbank Memorial Park  43.692028 -79.448924   
807    Central Toronto            Lawrence Park Ravine  43.726963 -79.394382   
808    Central Toronto              Zodiac Swim School  43.728532 -79.382860   
809    Central Toronto  TTC Bus #162 - Lawrence-Donway  43.728026 -79.382805   
1163  Downtown Toronto                   Rosedale Park  43.682328 -79.378934   
1164  Downtown Toronto                    Whitney Park  43.682036 -79.373788   
1165  Downtown Toronto            Alex Murray Parkette  43.678300 -79.382773   
1166  Downtown Toronto                  Milkman's Lane  43.676352 -79.373842   
1266         Etobicoke           Lambton-Kingsway Park  43.657085 -79.508145   
1267         Etobicoke              Humber River Falls  43.655617 -79.501702   

               Category  Borough_ID  Cluster Labels 1st Most Common Venue  \
0                  Park           0               0                  Park   
1     Food & Drink Shop           0               0                  Park   
249                Park           5               0                  Park   
250       Women's Store           5               0                  Park   
251                Pool           5               0                  Park   
252                Park           5               0                  Park   
807                Park           8               0                  Park   
808         Swim School           8               0                  Park   
809            Bus Line           8               0                  Park   
1163         Playground           1               0                  Park   
1164               Park           1               0                  Park   
1165               Park           1               0                  Park   
1166              Trail           1               0                  Park   
1266               Park           4               0                 River   
1267              River           4               0                 River   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0        Food & Drink Shop         Women's Store           Curling Ice   
1        Food & Drink Shop         Women's Store           Curling Ice   
249          Women's Store                  Pool          Cupcake Shop   
250          Women's Store                  Pool          Cupcake Shop   
251          Women's Store                  Pool          Cupcake Shop   
252          Women's Store                  Pool          Cupcake Shop   
807            Swim School              Bus Line         Women's Store   
808            Swim School              Bus Line         Women's Store   
809            Swim School              Bus Line         Women's Store   
1163            Playground                 Trail         Women's Store   
1164            Playground                 Trail         Women's Store   
1165            Playground                 Trail         Women's Store   
1166            Playground                 Trail         Women's Store   
1266                  Park      Cuban Restaurant            Donut Shop   
1267                  Park      Cuban Restaurant            Donut Shop   

     5th Most Common Venue  
0                Drugstore  
1                Drugstore  
249             Donut Shop  
250             Donut Shop  
251             Donut Shop  
252             Donut Shop  
807            Curling Ice  
808            Curling Ice  
809            Curling Ice  
1163          Cupcake Shop

In [251]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough                              Venue      V_Lat     V_Long  \
477     East York                   Danforth & Jones  43.684352 -79.334792   
478     East York                           The Path  43.683923 -79.335007   
479     East York                 Sammon Convenience  43.686951 -79.335007   
817          York                       Maison Birks  43.705857 -79.516102   
818          York                       Grattan Park  43.706222 -79.521705   
819          York          Olympic convenience store  43.704486 -79.515789   
826    North York                  Kitchen Food Fair  43.751298 -79.401393   
827    North York                    Tournament Park  43.751257 -79.399717   
1093  Scarborough                 McNicoll & Brimley  43.815461 -79.281716   
1094  Scarborough                    Port Royal Park  43.815477 -79.289773   
1095  Scarborough  Milliken Public School Playground  43.815383 -79.289867   

               Category  Borough_ID  Cluster Labels 1st Most Common Venue  \
477        Intersection           3               2                  Park   
478                Park           3               2                  Park   
479   Convenience Store           3               2                  Park   
817       Jewelry Store           5               2                  Park   
818                Park           5               2                  Park   
819   Convenience Store           5               2                  Park   
826   Convenience Store           0               2                  Park   
827                Park           0               2                  Park   
1093       Intersection           2               2            Playground   
1094               Park           2               2            Playground   
1095         Playground           2               2            Playground   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
477      Convenience Store          Intersection         Women's Store   
478      Convenience Store          Intersection         Women's Store   
479      Convenience Store          Intersection         Women's Store   
817          Jewelry Store     Convenience Store         Women's Store   
818          Jewelry Store     Convenience Store         Women's Store   
819          Jewelry Store     Convenience Store         Women's Store   
826      Convenience Store         Women's Store           Curling Ice   
827      Convenience Store         Women's Store           Curling Ice   
1093                  Park          Intersection         Women's Store   
1094                  Park          Intersection         Women's Store   
1095                  Park          Intersection         Women's Store   

     5th Most Common Venue  
477            Curling Ice  
478            Curling Ice  
479            Curling Ice  
817            Curling Ice  
818            Curling Ice  
819            Curling Ice  
826              Drugstore  
827              Drugstore  
1093          Cupcake Shop  
1094          Cupcake Shop  
1095          Cupcake Shop

In [252]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 7, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough                                Venue      V_Lat     V_Long  \
767   North York                      Strathburn Park  43.721765 -79.532854   
768   North York                             Triple A  43.722412 -79.528716   
1314   Etobicoke  The Artisan Cheese and Food Gallery  43.638785 -79.499953   
1315   Etobicoke                        Woodford Park  43.633152 -79.496266   

            Category  Borough_ID  Cluster Labels 1st Most Common Venue  \
767   Baseball Field           0               7        Baseball Field   
768     Food Service           0               7        Baseball Field   
1314   Deli / Bodega           4               7        Baseball Field   
1315  Baseball Field           4               7        Baseball Field   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
767           Food Service         Women's Store     Electronics Store   
768           Food Service         Women's Store     Electronics Store   
1314         Deli / Bodega         Women's Store           Escape Room   
1315         Deli / Bodega         Women's Store           Escape Room   

            5th Most Common Venue  
767                     Drugstore  
768                     Drugstore  
1314  Eastern European Restaurant  
1315  Eastern European Restaurant

In [148]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 5, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough                              Venue      V_Lat  \
0           North York                    Brookbanks Park  43.751976   
1           North York                      Variety Store  43.751974   
249               York                         Nairn Park  43.690654   
250               York                      Maximum Woman  43.690651   
251               York                     Fairbanks Pool  43.691959   
252               York             Fairbank Memorial Park  43.692028   
477          East York                   Danforth & Jones  43.684352   
478          East York                           The Path  43.683923   
479          East York                 Sammon Convenience  43.686951   
807    Central Toronto               Lawrence Park Ravine  43.726963   
808    Central Toronto                 Zodiac Swim School  43.728532   
809    Central Toronto     TTC Bus #162 - Lawrence-Donway  43.728026   
817               York                       Maison Birks  43.705857   
818               York                       Grattan Park  43.706222   
819               York          Olympic convenience store  43.704486   
826         North York                  Kitchen Food Fair  43.751298   
827         North York                    Tournament Park  43.751257   
1093       Scarborough                 McNicoll & Brimley  43.815461   
1094       Scarborough                    Port Royal Park  43.815477   
1095       Scarborough  Milliken Public School Playground  43.815383   
1163  Downtown Toronto                      Rosedale Park  43.682328   
1164  Downtown Toronto                       Whitney Park  43.682036   
1165  Downtown Toronto               Alex Murray Parkette  43.678300   
1166  Downtown Toronto                     Milkman's Lane  43.676352   
1266         Etobicoke              Lambton-Kingsway Park  43.657085   
1267         Etobicoke                 Humber River Falls  43.655617   

         V_Long           Category  Borough_ID  Cluster Labels  \
0    -79.332140               Park           0               3   
1    -79.333114  Food & Drink Shop           0               3   
249  -79.456300               Park           5               3   
250  -79.456333      Women's Store           5               3   
251  -79.448922               Pool           5               3   
252  -79.448924               Park           5               3   
477  -79.334792       Intersection           3               3   
478  -79.335007               Park           3               3   
479  -79.335007  Convenience Store           3               3   
807  -79.394382               Park           8               3   
808  -79.382860        Swim School           8               3   
809  -79.382805           Bus Line           8               3   
817  -79.516102      Jewelry Store           5               3   
818  -79.521705               Park           5               3   
819  -79.515789  Convenience Store           5               3   
826  -79.401393  Convenience Store           0               3   
827  -79.399717               Park           0               3   
1093 -79.281716       Intersection           2               3   
1094 -79.289773               Park           2               3   
1095 -79.289867         Playground           2               3   
1163 -79.378934         Playground           1               3   
1164 -79.373788               Park           1               3   
1165 -79.382773               Park           1               3   
1166 -79.373842              Trail           1               3   
1266 -79.508145               Park           4               3   
1267 -79.501702              River           4               3   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                     Park     Food & Drink Shop         Women's Store   
1                     Park     Food & Drink Shop         Women's Store   
249                   Park         Women's Store                 

In [253]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough                                  Venue      V_Lat  \
8     Downtown Toronto                       Roselle Desserts  43.653447   
9     Downtown Toronto                          Tandem Coffee  43.653559   
10    Downtown Toronto                 Cooper Koo Family YMCA  43.653249   
11    Downtown Toronto                    Body Blitz Spa East  43.654735   
12    Downtown Toronto                         Impact Kitchen  43.656369   
...                ...                                    ...        ...   
1324         Etobicoke                                   RONA  43.629393   
1325         Etobicoke                             McDonald's  43.630007   
1326         Etobicoke  Koala Tan Tanning Salon & Sunless Spa  43.631370   
1327         Etobicoke                          Value Village  43.631269   
1328         Etobicoke                   Kingsway Boxing Club  43.627254   

         V_Long                Category  Borough_ID  Cluster Labels  \
8    -79.362017                  Bakery           1               4   
9    -79.361809             Coffee Shop           1               4   
10   -79.358008     Distribution Center           1               4   
11   -79.359874                     Spa           1               4   
12   -79.356980              Restaurant           1               4   
...         ...                     ...         ...             ...   
1324 -79.518320          Hardware Store           4               4   
1325 -79.518041    Fast Food Restaurant           4               4   
1326 -79.519006           Tanning Salon           4               4   
1327 -79.518238  Thrift / Vintage Store           4               4   
1328 -79.526684                     Gym           4               4   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
8              Coffee Shop                  Park                Bakery   
9              Coffee Shop                  Park                Bakery   
10             Coffee Shop                  Park                Bakery   
11             Coffee Shop                  Park                Bakery   
12             Coffee Shop                  Park                Bakery   
...                    ...                   ...                   ...   
1324         Tanning Salon          Burger Joint       Supplement Shop   
1325         Tanning Salon          Burger Joint       Supplement Shop   
1326         Tanning Salon          Burger Joint       Supplement Shop   
1327         Tanning Salon          Burger Joint       Supplement Shop   
1328         Tanning Salon          Burger Joint       Supplement Shop   

     4th Most Common Venue 5th Most Common Venue  
8                     Café               Theater  
9                     Café               Theater  
10                    Café               Theater  
11                    Café               Theater  
12                    Café               Theater  
...                    ...                   ...  
1324           Wings Joint        Discount Store  
1325           Wings Joint        Discount Store  
1326           Wings Joint        Discount Store  
1327           Wings Joint        Discount Store  
1328           Wings Joint        Discount Store  

[872 rows x 12 columns]